In [1]:
from typing import AnyStr
import os
os.chdir("..")
os.chdir("src")
from data_cleaning import DataCleaning
from nltk.stem import RSLPStemmer
import nltk
from unidecode import unidecode
import re
from gensim.models import CoherenceModel
from gensim.models.ldamulticore import LdaMulticore
import gensim.corpora as corpora
import matplotlib.pyplot as plt

from wordcloud import WordCloud
# from pt_lemmatizer import Lemmatizer
nltk.download('stopwords')
os.chdir("..")

[nltk_data] Downloading package stopwords to /home/bruno/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!



## - Fazer otimizacao bayesiana com:
	-  lemma vs stemmer
	-  alem de filtro de 1500x 1000 x 500 vs sem filtro (pegar o resultado melhor de todos)


## - visualizacao com pca umap 
## - avaliacao com outras metricas



precisa baixa o coisa do spacy com `python -m spacy download pt_core_news_md`

In [2]:
def word_cloud(stopwords, modelo, n_topicos, figsize=(20,20)):
    '''
    Display de word cloud.

    Parameters
    ----------
    stopwords : stopwords

    modelo : modelo usado

    n_topicos : número de tópicos

    Returns
    -------
    ax : word_clud 
    '''   
    cloud = WordCloud(stopwords=stopwords,
                    background_color='white',
                    width=2500,
                    height=1800,
                    max_words=7,
                    colormap='tab10',
                    prefer_horizontal=1.0)
    topics = modelo.show_topics(formatted=False)
    fig, axes = plt.subplots(1, n_topicos, figsize=figsize, sharex=True, sharey=True)
    for i, ax in enumerate(axes.flatten()):
        fig.add_subplot(ax)
        topic_words = dict(topics[i][1])
        cloud.generate_from_frequencies(topic_words, max_font_size=400)
        plt.gca().imshow(cloud)
        plt.gca().set_title('Topic ' + str(i), fontdict=dict(size=16))
        plt.gca().axis('off')
    plt.subplots_adjust(wspace=0, hspace=0)
    plt.axis('off')
    plt.margins(x=0, y=0)
    plt.tight_layout()
    plt.show()    
    return ax    


In [3]:
cleaning_pipeline = DataCleaning()
df = cleaning_pipeline.run()

2024-04-01 23:14:06 - INFO - Data loaded!
2024-04-01 23:14:06 - INFO - Null values cleaned!
/home/bruno/mestrado-ufrgs/mestrado-ufrgs-cmp617-tce/src/data_cleaning.py:94: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_final["ANO_LICITACAO"] = df_final["ANO_LICITACAO"].replace(
2024-04-01 23:14:06 - INFO - Data types asserted!
2024-04-01 23:14:06 - INFO - Full data cleaned!


In [4]:
df = df[df["ANO_LICITACAO"]>=2021]

## NLP treatment

In [5]:
def remove_stop_words(words):
    stop_words = []

    with open("stop_words.txt", "r") as file:
        for row in file:
            stop_words.append(row.strip())

    return [word for word in words if word.lower() not in stop_words]

def preprocess(x: AnyStr) -> str:

    special_chars = "¨'!#$%&()*+,./:;<=>?@[\]^_`{|}~"
    new_x = x.replace('"',' ')
    for c in special_chars:
        new_x = new_x.replace(c,' ') # Removes special characters
    new_x = re.sub(r'[^\w\s]', ' ', new_x) # Removes punctuation
    new_x = re.sub("http\S+", ' ',new_x) # Removes links
    new_x = re.sub("@\w+", ' ',new_x) # Removes @
    new_x = re.sub('#\S+', ' ',new_x) # Removes hashtags
    new_x = re.sub('[0-9]+', ' ',new_x) # Removes numbers
    new_x = unidecode(new_x) # Removes accents
    new_x = re.sub("\s+", ' ',new_x) # Removes spaces

    new_x = ' '.join([word for word in new_x.split() if len(word) > 2])
    
    new_x = new_x.strip()
    return new_x

def stemmer_pt(words):
    
    stemmer = RSLPStemmer()
    return [stemmer.stem(word) for word in words]


In [6]:
df = df.assign(
    DS_OBJETO_NLP=df["DS_OBJETO"]
    .apply(lambda x: nltk.word_tokenize(x.lower(), language="portuguese")) # Tokenize
    .apply(lambda x: [preprocess(word) for word in x]) # Other preprocessing
    .apply(lambda x: list(filter(None, x))) # Removes items with none
    .apply(remove_stop_words) # Removes stop words
    .apply(lambda x: [word for word in x if "rs" not in word]) # Remove tokens containing "rs" (which are cities)
    .apply(stemmer_pt) # Applies stemming
)

In [7]:
vec = df["DS_OBJETO_NLP"].values.tolist()

In [22]:
# id2word = corpora.Dictionary(vec)

# # tokens_a_remover = [token for token, freq in id2word.dfs.items() if freq < 1000]
# # id2word.filter_tokens(bad_ids=tokens_a_remover)
# # id2word.compactify()

# # Reconstrua o corpus após remover as palavras
# corpus = [id2word.doc2bow(text) for text in vec]


# lda_model = ldamulticore.LdaMulticore(corpus=corpus,
#                                       id2word=id2word,
#                                       num_topics=8, 
#                                       random_state=42,
#                                       chunksize=120,
#                                       passes=8,
#                                       alpha=0.01,
#                                       eta=0.91,
#                                       per_word_topics=True)

# coherence_model_lda = CoherenceModel(model=lda_model, texts=vec, dictionary=id2word, coherence='c_v')
# coherence_lda = coherence_model_lda.get_coherence()

# temos em torno de 0.44-0.45 nesses casos

2024-04-01 17:06:40 - INFO - adding document #0 to Dictionary<0 unique tokens: []>
2024-04-01 17:06:40 - INFO - adding document #10000 to Dictionary<7405 unique tokens: ['erechim', 'fundaca', 'hospital', 'medic', 'ter']...>
2024-04-01 17:06:40 - INFO - adding document #20000 to Dictionary<10865 unique tokens: ['erechim', 'fundaca', 'hospital', 'medic', 'ter']...>
2024-04-01 17:06:40 - INFO - adding document #30000 to Dictionary<13356 unique tokens: ['erechim', 'fundaca', 'hospital', 'medic', 'ter']...>
2024-04-01 17:06:40 - INFO - adding document #40000 to Dictionary<15592 unique tokens: ['erechim', 'fundaca', 'hospital', 'medic', 'ter']...>
2024-04-01 17:06:41 - INFO - adding document #50000 to Dictionary<17701 unique tokens: ['erechim', 'fundaca', 'hospital', 'medic', 'ter']...>
2024-04-01 17:06:41 - INFO - adding document #60000 to Dictionary<19294 unique tokens: ['erechim', 'fundaca', 'hospital', 'medic', 'ter']...>
2024-04-01 17:06:41 - INFO - adding document #70000 to Dictionary<

## Opt - Stemmer

In [8]:
import optuna

# Defining an objective function to be optimized
def bayesian_opt_objective(trial, id2word, corpus, vec):

    num_topics = trial.suggest_int('num_topics', 6, 9, step=1)
    chunksize = trial.suggest_int('chunksize', 80, 180, step=10)
    passes = trial.suggest_int('passes', 5, 20, step=1)
    alpha = trial.suggest_float('alpha', 0.01, 1, step=0.01)
    eta = trial.suggest_float('eta', 0.01, 0.15, step=0.01)
    decay = trial.suggest_float('decay', 0.5, 1, step=0.1)

    lda_model = LdaMulticore(corpus=corpus,
                               id2word=id2word,
                               num_topics=num_topics,
                               chunksize=chunksize,
                               passes=passes,
                               alpha=alpha,
                               eta=eta,
                               decay=decay,                               
                               random_state=42, 
                               workers=12,
                               per_word_topics=True)
    # Prediction
    coherence_model_lda = CoherenceModel(model=lda_model, texts=vec, dictionary=id2word, coherence='c_v')
    coherence_lda = coherence_model_lda.get_coherence()

    return coherence_lda

In [34]:
id2word = corpora.Dictionary(vec)

tokens_a_remover = [token for token, freq in id2word.dfs.items() if freq < 0]
id2word.filter_tokens(bad_ids=tokens_a_remover)
id2word.compactify()

# Reconstrua o corpus após remover as palavras
corpus = [id2word.doc2bow(text) for text in vec]

2024-04-01 23:27:03 - INFO - adding document #0 to Dictionary<0 unique tokens: []>
2024-04-01 23:27:03 - INFO - adding document #10000 to Dictionary<7405 unique tokens: ['erechim', 'fundaca', 'hospital', 'medic', 'ter']...>
2024-04-01 23:27:03 - INFO - adding document #20000 to Dictionary<10865 unique tokens: ['erechim', 'fundaca', 'hospital', 'medic', 'ter']...>
2024-04-01 23:27:03 - INFO - adding document #30000 to Dictionary<13356 unique tokens: ['erechim', 'fundaca', 'hospital', 'medic', 'ter']...>
2024-04-01 23:27:03 - INFO - adding document #40000 to Dictionary<15592 unique tokens: ['erechim', 'fundaca', 'hospital', 'medic', 'ter']...>
2024-04-01 23:27:03 - INFO - adding document #50000 to Dictionary<17701 unique tokens: ['erechim', 'fundaca', 'hospital', 'medic', 'ter']...>
2024-04-01 23:27:03 - INFO - adding document #60000 to Dictionary<19294 unique tokens: ['erechim', 'fundaca', 'hospital', 'medic', 'ter']...>
2024-04-01 23:27:03 - INFO - adding document #70000 to Dictionary<

In [41]:
corpus[0]

[(0, 1), (1, 1), (2, 2), (3, 1), (4, 1)]

In [10]:
study = optuna.create_study(direction="maximize")
study.optimize(lambda trial: bayesian_opt_objective(trial, id2word, corpus, vec), n_trials=2)
trial = study.best_trial

print(f'Best Coherence Score - Filter 1000 = {trial.value}')
print(f'Best Hyperparameters - Filter 1000 = {trial.params}')

[I 2024-04-01 23:20:08,959] A new study created in memory with name: no-name-02b46dc1-5bdf-4728-aa2d-f60e4294ca91
2024-04-01 23:20:08 - INFO - using serial LDA version on this node
2024-04-01 23:20:08 - INFO - running online LDA training, 7 topics, 5 passes over the supplied corpus of 128038 documents, updating every 960 documents, evaluating every ~9600 documents, iterating 50x with a convergence threshold of 0.001000
2024-04-01 23:20:08 - INFO - training LDA model using 12 processes
2024-04-01 23:20:09 - INFO - PROGRESS: pass 0, dispatched chunk #0 = documents up to #80/128038, outstanding queue size 1
2024-04-01 23:20:09 - INFO - PROGRESS: pass 0, dispatched chunk #1 = documents up to #160/128038, outstanding queue size 2
2024-04-01 23:20:09 - INFO - PROGRESS: pass 0, dispatched chunk #2 = documents up to #240/128038, outstanding queue size 3
2024-04-01 23:20:09 - INFO - PROGRESS: pass 0, dispatched chunk #3 = documents up to #320/128038, outstanding queue size 4
2024-04-01 23:20:09

Best Coherence Score - Filter 1000 = 0.35931267652019805
Best Hyperparameters - Filter 1000 = {'num_topics': 7, 'chunksize': 80, 'passes': 5, 'alpha': 0.45, 'eta': 0.01, 'decay': 0.6}


In [15]:
type_nlp_method = "stemmer"


In [12]:
n_filter = 0

In [16]:
results = {}
results["filter"] = n_filter
results["nlp_normalization_method"] = type_nlp_method
results["best_score"] = trial.value
results["params"] = trial.params

In [11]:
import json

In [19]:
output_path = f"src/opt_outputs/results_{type_nlp_method}_with_filter_{n_filter}.json"
with open(output_path, "w") as json_file:
    json.dump(results, json_file)

In [18]:
pwd

'/home/bruno/mestrado-ufrgs/mestrado-ufrgs-cmp617-tce'

In [38]:
import spacy

In [39]:
nlp = spacy.load("pt_core_news_ma", disable=['parser', 'tagger','ner'])

OSError: [E050] Can't find model 'pt_core_news_ma'. It doesn't seem to be a Python package or a valid path to a data directory.

In [19]:
results

{'type_nlp_method': 'stemmer',
 'best_score': 0.42353980407695535,
 'params': {'num_topics': 8,
  'chunksize': 180,
  'passes': 9,
  'alpha': 0.62,
  'eta': 0.060000000000000005,
  'decay': 0.6}}

In [11]:
trial.value

0.42353980407695535

## Visualization

In [ ]:
from sklearn.decomposition import PCA
pca = PCA(n_components=2)
X_pca = pca.fit_transform(X)  # X é a matriz de features


In [ ]:
import umap
umap_model = umap.UMAP(n_components=2)
X_umap = umap_model.fit_transform(X)  # X é a matriz de features


In [ ]:
!pip install umap-learn

In [ ]:
import matplotlib.pyplot as plt

# Para PCA
plt.figure(figsize=(8, 6))
plt.scatter(X_pca[:, 0], X_pca[:, 1], c=labels, cmap='viridis', s=50)
plt.title('PCA Clustering')
plt.xlabel('Principal Component 1')
plt.ylabel('Principal Component 2')
plt.colorbar()
plt.show()

In [ ]:
# Para UMAP
plt.figure(figsize=(8, 6))
plt.scatter(X_umap[:, 0], X_umap[:, 1], c=labels, cmap='viridis', s=50)
plt.title('UMAP Clustering')
plt.xlabel('UMAP Dimension 1')
plt.ylabel('UMAP Dimension 2')
plt.colorbar()
plt.show()
